# Imports

In [1]:
import pandas as pd
from unidecode import unidecode
import numpy as np
from datetime import datetime
import json

In [2]:
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)
pd.set_option('display.width', 1000)

# Opening

In [3]:
df = pd.read_excel(
    r"..\data\tbl\dados_reais.xlsx"
)
df

Carimbo de data/hora                                         Nome Número do prontuário Tipo de atendimento     Data atendimento                                 Data de nascimento             Idade                  Sexo                         Cidade e bairro que reside                Escolaridade Período em que trabalha/estuda Há possibilidade de realizar lanches no local de estudo? Período em que trabalha Há a possibilidade de realizar lanches no local de trabalho?                                          Profissão          Renda familiar Quantas pessoas moram no domicílio (contando com você)                 Motivo pela procura do ambulatório                     Apresenta alguma doença? Apresenta antecedentes familiares de alguma doença crônica? (DM, HAS, dislipidemia...)                Faz uso de medicamentos contínuos?  Faz uso de suplementos ou complementos alimentares? Frequência de evacuação Consistência da evacuação: Pratica atividade física regularmente?  \
0    2024-03-11 08:18:36.001000                                            .                    .           Avaliação  2024-03-12 00:00:00                                                  .               NaN              Feminino                                                  .                       Outra                     Não estuda                                                Não                  Não trabalha                                                Não                                                            .                 Não sei                                                  .                                                      .                                       Outras                                                  .                                                                                      .                                                  .           <3x por semana                     Tipo 7                                    Não   
1    2024-03-11 10:36:19.952000                                            .                    .          Orientação  2024-03-11 00:00:00                                                  .                 .  Prefiro não informar                                                  .                       Outra                     Não estuda                                                Não                  Não trabalha                                                Não                                                            .                 Não sei                                                  .                                                      .                                       Outras                                                  .                                                                                      .                                                  .           <3x por semana                     Tipo 7                                    Não   
2    2025-02-21 11:41:51.441000                         .Flavio Russo Pinto                  8860           Avaliação  2025-02-21 00:00:00                                         28/08/1964                61              Feminino                               Sao Vicente- Centro     Ensino superior completo                          Manhã                                                NaN                           NaN                                                NaN                                         Funcionario publico   3 a 5 salários mínimos                                              Duas                    Reeducação alimentar, perda de peso.                                          HAS                   Sim, pai diabetico e hipertenso                                                                   sim- para hipertensao                       Multivitaminico, vitamina C                    Diária                     Tipo 3                                    Sim   
3    2023-05-15 12:53:11.617000                

In [4]:
print(list(df.columns))

['Carimbo de data/hora', 'Nome', 'Número do prontuário', 'Tipo de atendimento', 'Data atendimento', 'Data de nascimento', 'Idade', 'Sexo', 'Cidade e bairro que reside', 'Escolaridade', 'Período em que trabalha/estuda', 'Há possibilidade de realizar lanches no local de estudo?', 'Período em que trabalha', 'Há a possibilidade de realizar lanches no local de trabalho?', 'Profissão', 'Renda familiar', 'Quantas pessoas moram no domicílio (contando com você)', 'Motivo pela procura do ambulatório', 'Apresenta alguma doença?', 'Apresenta antecedentes familiares de alguma doença crônica? (DM, HAS, dislipidemia...)', 'Faz uso de medicamentos contínuos? ', 'Faz uso de suplementos ou complementos alimentares?', 'Frequência de evacuação', 'Consistência da evacuação:', 'Pratica atividade física regularmente?', 'Se sim: qual atividade, frequência semanal e duração? (intensidade,peso)', 'Café da manhã:', 'Lanche da manhã (se houver):', 'Almoço:', 'Lanche da tarde:', 'Jantar:', 'Ceia (se houver):', 'Ve

In [4]:
df_headers = df.drop(index=range(0, len(df)))
df_headers.to_csv(
    r"..\data\tbl\headers.csv",
    sep=";",
    index=False,
    encoding="utf-8",
    )

# Transformações

## Pacientes

In [5]:
df_pacientes = df[['Nome', 'Sexo', 'Data de nascimento', 'Carimbo de data/hora']]
df_pacientes_original = df_pacientes.copy(deep=True)
df_pacientes


Nome                  Sexo                                 Data de nascimento        Carimbo de data/hora
0                                              .              Feminino                                                  .  2024-03-11 08:18:36.001000
1                                              .  Prefiro não informar                                                  .  2024-03-11 10:36:19.952000
2                           .Flavio Russo Pinto               Feminino                                         28/08/1964  2025-02-21 11:41:51.441000
3                               Adesia dos Anjos              Feminino                                           29/04/71  2023-05-15 12:53:11.617000
4                        Adriana Aparecida Simão              Feminino                                         29/10/1973  2023-04-03 12:10:35.366000
5                         Adriana Lucia de Souza              Feminino                                         28/04/1970  2024-04-22 11:15:34.772000
6                        Adriana Melo de Andrade              Feminino                                             030264  2024-03-11 09:33:04.566000
7                        Adriana Melo de Andrade              Feminino                                         03/02/1964  2025-02-19 11:40:58.472000
8                       Adriana Melo de Andrade               Feminino                                         03/02/1964  2023-03-13 10:35:05.977000
9                                          Agata              Feminino                                         27 04 2006  2024-09-16 10:21:12.319000
10                          Alair Teresinha Luiz              Feminino                                         15/03/1960  2024-09-09 10:18:14.095000
11              Alexandre Donaire pereira jorge              Masculino                                         27/06/2003  2024-09-16 09:43:24.324000
12                         Aline Fonseca Martins              Feminino                                         18/01/1999  2024-10-21 11:50:23.290000
13              Alyne Cristine Martins e Martins              Feminino                                         02/11/1990  2023-03-20 10:04:24.747000
14                    Amanda Cristina de Santana              Feminino                                         26/01/1996  2024-03-04 11:01:44.815000
15                  Amarilis de Almeida Pereira               Feminino                                           19011937  2023-04-10 10:48:19.899000
16                     Ana Carolina Ramos Costas              Feminino                                        .04/04/2000  2023-09-04 11:13:50.585000
17                  Ana Carolina Spinelli Castex              Feminino                                           28081990  2023-05-08 12:35:33.500000
18                                     Ana Clara              Feminino                                         17/06/2002  2023-02-24 10:07:18.820000
19            Ana Claudia gonçalves de Siqueira               Feminino                                         14/01/1964  2024-09-09 08:58:56.946000
20                          Ana Eli de Oliveira               Feminino                                         12/06/1938  2023-05-29 12:10:00.439000
21                             Ana Lu Viera Dias              Feminino                                         01/02/1973  2023-04-10 10:20:56.699000
22                    Ana Luiza Congedo Carrieni              Feminino                                         27/07/1987  2023-09-25 09:44:36.603000
23                Ana Luiza de Oliveira Ribeiro               Feminino                                             141172  2023-08-21 10:29:17.282000
24                        Ana Maria Gentil Alves              Feminino                                         31/01/1986  2023-10-02 11:54:35.827000
25                       Ana Paula Dantas Barata              Feminino                                           08071993  2023-02-27 11:07:10.2

In [6]:
def format_date_nasc(date: str) -> str:
    if pd.isna(date):
        return ''
    
    try:
        date: str = str(date).replace('-', '/').replace('.', '').replace(' ', '').replace('?', '/').strip()
        
        if len(date) == 8 and '/' not in date:
            date = f'{date[:2]}/{date[2:4]}/{date[4:]}'
            
        if len(date) == 8 and '/' in date:
            date = f'{date[:6]}/{"19" if int(date[6:]) > 25 else "20"}{date[6:]}'    
        
        elif len(date) == 6:
            date = f'{date[:2]}/{date[2:4]}/{"19" if int(date[4:]) > 25 else "20"}{date[4:]}'
            
        date: str = str(date).replace('//', '/')
        
    except Exception as e:
        print(e)
    
    return date

In [7]:
df_pacientes['Nome'] = df_pacientes['Nome'].apply(lambda x: unidecode(x).replace('.', '').strip().title())
df_pacientes['Data de nascimento'] = df_pacientes['Data de nascimento'].apply(format_date_nasc)

C:\Users\Arklok\AppData\Local\Temp\ipykernel_2968\3073021553.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_pacientes['Nome'] = df_pacientes['Nome'].apply(lambda x: unidecode(x).replace('.', '').strip().title())
C:\Users\Arklok\AppData\Local\Temp\ipykernel_2968\3073021553.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_pacientes['Data de nascimento'] = df_pacientes['Data de nascimento'].apply(format_date_nasc)


In [8]:
df_pacientes = df_pacientes[
    (~df_pacientes['Nome'].str.contains('Teste')) &
    (~df_pacientes['Nome'].str.contains('Alun')) &
    (df_pacientes['Nome'].str.split(' ').str.len() > 2) &
    (df_pacientes['Data de nascimento'].str.contains('^([0-2][0-9]|3[01])/(0[1-9]|1[0-2])/(19|20)[0-9]{2}$'))
]

C:\Users\Arklok\AppData\Local\Temp\ipykernel_2968\3449170069.py:5: UserWarning: This pattern is interpreted as a regular expression, and has match groups. To actually get the groups, use str.extract.
  (df_pacientes['Data de nascimento'].str.contains('^([0-2][0-9]|3[01])/(0[1-9]|1[0-2])/(19|20)[0-9]{2}$'))


In [9]:
df_pacientes_insert = df_pacientes.dropna(subset=['Sexo', 'Nome', 'Data de nascimento'])\
    .sort_values(by=['Nome', 'Carimbo de data/hora'], ascending=[True, True])\
        .drop_duplicates(subset=['Nome'], keep='first')\
            .drop(columns=['Carimbo de data/hora'])
df_pacientes_insert

Nome       Sexo Data de nascimento
3                               Adesia Dos Anjos   Feminino         29/04/1971
4                        Adriana Aparecida Simao   Feminino         29/10/1973
5                         Adriana Lucia De Souza   Feminino         28/04/1970
8                        Adriana Melo De Andrade   Feminino         03/02/1964
261                        Aide De Souza Pacheco   Feminino         30/11/2022
10                          Alair Teresinha Luiz   Feminino         15/03/1960
11               Alexandre Donaire Pereira Jorge  Masculino         27/06/2003
12                         Aline Fonseca Martins   Feminino         18/01/1999
13              Alyne Cristine Martins E Martins   Feminino         02/11/1990
14                    Amanda Cristina De Santana   Feminino         26/01/1996
15                   Amarilis De Almeida Pereira   Feminino         19/01/1937
16                     Ana Carolina Ramos Costas   Feminino         04/04/2000
17                  Ana Carolina Spinelli Castex   Feminino         28/08/1990
19             Ana Claudia Goncalves De Siqueira   Feminino         14/01/1964
20                           Ana Eli De Oliveira   Feminino         12/06/1938
21                             Ana Lu Viera Dias   Feminino         01/02/1973
22                    Ana Luiza Congedo Carrieni   Feminino         27/07/1987
23                 Ana Luiza De Oliveira Ribeiro   Feminino         14/11/1972
24                        Ana Maria Gentil Alves   Feminino         31/01/1986
25                       Ana Paula Dantas Barata   Feminino         08/07/1993
26                    Andrea Castello Dos Santos   Feminino         06/04/1971
27                         Andres Abellan Hellin  Masculino         07/03/1968
28                            Andrew Rocha Silva  Masculino         16/03/2000
29              Angela Maria Franzese De Santana   Feminino         29/01/1965
30                            Angela Maria Verre   Feminino         24/03/1965
31               Angelina Goncalves Couto Hellin   Feminino         17/04/1966
32              Angelo Antonio Pires De Oliveira  Masculino         14/11/1991
33                      Antonio Carregalo Martin  Masculino         28/09/1953
34                           Audra Liz Magalhaes   Feminino         08/10/1980
35                     Auria Cavalcante De Souza   Feminino         18/11/1967
36                     Beatriz Da Silva Matildes   Feminino         10/10/2000
37                 Carmen Oliveiro Ribeiro Matos   Feminino         20/04/1979
39                      Caue De Sa Dias Morgardo  Masculino         21/04/2004
40                     Cecilia De Souza Carvalho   Feminino         28/02/1978
41    Celia Cristina Dos Santos Bispo Bartolotto   Feminino         12/08/1976
42                 Celia Dos Santos Cruz Santana   Feminino         21/08/1974
43                       Celia Rodrigues Ribeiro   Feminino         02/01/1960
44                     Cibele Rodrigues Da Silva   Feminino         17/06/1988
45                       Cintia Maria Dos Santos   Feminino         28/05/1987
46                 Claudia Ventura Da Cruz Souza   Feminino         24/08/1962
47                      Clayton Moreira Da Silva  Masculino         15/11/1989
48                       Clecio Augusto Da Silva  Masculino         18/12/1970
51                       Dalva Aparecida Martins   Feminino         19/05/1963
52                       Daniel Barreto Monteiro  Masculino         10/05/2001
54                          Daphne Silva Santana   Feminino         10/01/1996
55                       Debora Flori De Azevedo   Feminino         13/02/1977
57                Diego Andrade Alves De Freitas  Masculino         17/05/1984
59                  Donizete Oliveira Dos Santos  Masculino         23/03/1973
60                          Edilene Izidio Alves   Feminino         07/10/1966
62                Edson Francisco Da Silva Alvim  Masculino         09/09/1973
63             

In [10]:
df_pacientes_not_insert = df_pacientes_original[df_pacientes_original.index.isin(df_pacientes.index) == False][['Nome', 'Sexo', 'Data de nascimento']]
df_pacientes_not_insert

Nome                  Sexo Data de nascimento
0                                            .              Feminino                  .
1                                            .  Prefiro não informar                  .
9                                        Agata              Feminino         27 04 2006
18                                   Ana Clara              Feminino         17/06/2002
38                                Caroline Cao              Feminino           29021996
49                           Cristriane Franco              Feminino         21/09/1974
50                              Cyra Fernandes              Feminino         20/05/1964
53                            Daniela Goldberg              Feminino         05/10/1979
56                               Débora Franco              Feminino         27/09/1994
58                                 Diva Ramona              Feminino         23/02/1970
61                                  EDIMILSON              Masculino                 XX
82                                   frederico  Prefiro não informar           21101999
83                             Gabriel Pereira             Masculino         10/06/1996
86                            Gabriela Ribeiro              Feminino         16/10/2000
87                           Gabriela vicente               Feminino         10.12.1996
103                                  Isabella               Feminino         12/03/2003
108                             Jessica Silva               Feminino         23/10/1986
111                                     Joelma              Feminino           20061997
117                  Juliana Barboza da Silva                    NaN                NaN
144                               Luiz Torres              Masculino         23/07/1937
147                               Magali Lomão              Feminino         04/10/1972
154                              Marco antonio             Masculino           23/02/64
171               Maria José Justino Ferreira               Feminino         17/91/1967
177                          Mariani Lourenço               Feminino         13/09/2000
182                                   Marlene               Feminino                  .
190                            MICHELLE UEMURA              Feminino           13031975
193                             Mirelle Vieira              Feminino         11/11/1987
201                           Natalya Vicente               Feminino         12/03/2001
218                                   Rodrigo              Masculino           08012006
221                                  Rosangela              Feminino         09/02/1982
225                             Sandra Massako              Feminino         24-01-1958
226                               Sangela Cruz              Feminino         08/06/2003
233                                     Sophia              Feminino         17/07/2006
241                                teste cezar             Masculino                www
247  VANESSA RAMOS  ALUNA 1 SEMESTRE NUTRIÇÃO               Feminino         28/02/2007
252                              VIVIAN SANTOS              Feminino           26091995
253                         Willian Giovannini             Masculino         30/12/1997
256                               Yasmin Gomes              Feminino         17/06/1994
257                    MARIANA NICOLA - ALUNA               Feminino              11111
259                            Bernadino Serra             Masculino         08/11/1943
267                                      TESTE              Feminino            1215464

## Retorno

In [11]:
df_retorno = df[df['Tipo de atendimento'] == 'retorno']
df_retorno

Carimbo de data/hora                       Nome Número do prontuário Tipo de atendimento Data atendimento Data de nascimento Idade Sexo Cidade e bairro que reside Escolaridade Período em que trabalha/estuda Há possibilidade de realizar lanches no local de estudo? Período em que trabalha Há a possibilidade de realizar lanches no local de trabalho? Profissão Renda familiar Quantas pessoas moram no domicílio (contando com você) Motivo pela procura do ambulatório Apresenta alguma doença? Apresenta antecedentes familiares de alguma doença crônica? (DM, HAS, dislipidemia...) Faz uso de medicamentos contínuos?  Faz uso de suplementos ou complementos alimentares? Frequência de evacuação Consistência da evacuação: Pratica atividade física regularmente? Se sim: qual atividade, frequência semanal e duração? (intensidade,peso) Café da manhã: Lanche da manhã (se houver): Almoço: Lanche da tarde: Jantar: Ceia (se houver): Verduras (alface, rúcula, almeirão, escarola, espinafre, acelga...)  \
117  2024-05-06 00:00:00  Juliana Barboza da Silva                  8806             retorno              NaN                NaN   NaN  NaN                        NaN          NaN                            NaN                                                NaN                           NaN                                                NaN                 NaN            NaN                                                NaN                                    NaN                      NaN                                                NaN                                                                     NaN                                                NaN                      NaN                        NaN                                    NaN                                                NaN                                  NaN                          NaN     NaN              NaN     NaN               NaN                                                NaN                    

    Verduras e legumes [Beterraba] Verduras e legumes [Berinjela] Verduras e legumes [Pepino] Verduras e legumes [Abobrinha] Verduras e legumes [Chuchu] Verduras [Acelga] Verduras [Agrião] Verduras [Alface] Verduras [Brócolis] Verduras [Chicória] Verduras [Couve Manteiga] Verduras [Couve-flor] Verduras [Escarola] Verduras [Espinafre] Verduras [Rúcula] Frutas cítricas [Laranja] Frutas cítricas [Tangerina/Mexerica/Bergamota] Frutas cítricas [Limão] Frutas cítricas [Abacaxi] Frutas cítricas [Acerola] Frutas cítricas [Morango] Frutas cítricas [Kiwi] Frutas cítricas [Maracujá] Outras frutas [Banana Nanica/Prata/Ouro/Maçã] Outras frutas [Goiaba] Outras frutas [Maçã] Outras frutas [Mamão] Outras frutas [Manga] Outras frutas [Melancia] Outras frutas [Melão] Outras frutas [Pera] Outras frutas [Pêssego] Outras frutas [Uva] Leguminosas [Feijões em geral (preto, carioca, branco)] Leguminosas [Feijão Preto] Leguminosas [Feijão Branco] Leguminosas [Lentilha] Leguminosas [Ervilha]  \
117                            NaN                            NaN                         NaN                            NaN                         NaN               NaN               NaN               NaN                 NaN                 NaN                       NaN                   NaN                 NaN                  NaN               NaN                       NaN                                            NaN                     NaN                       NaN                       NaN                       NaN                    NaN                        NaN                                           NaN                    NaN                  NaN                   NaN                   NaN                      NaN                   NaN                  NaN                     NaN                 NaN                                                NaN                             NaN                         NaN                    NaN                   NaN   

    Leguminosas [Soja] Leguminosas [Grão

## Anamnese

In [12]:
df_anamnese = df[df['Tipo de atendimento'] != 'retorno']
df_anamnese = df_anamnese[df_anamnese.index == 5]
df_anamnese

Carimbo de data/hora                    Nome Número do prontuário Tipo de atendimento     Data atendimento Data de nascimento Idade      Sexo Cidade e bairro que reside           Escolaridade Período em que trabalha/estuda Há possibilidade de realizar lanches no local de estudo? Período em que trabalha Há a possibilidade de realizar lanches no local de trabalho? Profissão          Renda familiar Quantas pessoas moram no domicílio (contando com você) Motivo pela procura do ambulatório Apresenta alguma doença? Apresenta antecedentes familiares de alguma doença crônica? (DM, HAS, dislipidemia...) Faz uso de medicamentos contínuos?  Faz uso de suplementos ou complementos alimentares? Frequência de evacuação Consistência da evacuação: Pratica atividade física regularmente? Se sim: qual atividade, frequência semanal e duração? (intensidade,peso)                                     Café da manhã: Lanche da manhã (se houver):                                            Almoço:  \
5  2024-04-22 11:15:34.772000  Adriana Lucia de Souza                 8814           Avaliação  2024-04-22 00:00:00         28/04/1970    53  Feminino               São vicente.  Ensino médio completo                     Não estuda                                                Não                  Não trabalha                                                Não             Coopera  1 a 2 salários mínimos                                                  1           Pela intolerância a lactose.                     DM 2  a vó materna faleceu por cancer de utero, e a ...                                                            Mediformina.  Sim, um suplemento para a menopausa, capsula p...           <3x por semana                     Tipo 1                                    Não                                                NaN                        Nescafé com leite de soja, adoça com adoçante ...  1 un. banana ou 1 un. maçã.  arroz, abobrinha, purê de batata ou mandioquin...   

                               Lanche da tarde:                                            Jantar:     Ceia (se houver): Verduras (alface, rúcula, almeirão, escarola, espinafre, acelga...) Verduras e legumes [Beterraba] Verduras e legumes [Berinjela] Verduras e legumes [Pepino] Verduras e legumes [Abobrinha] Verduras e legumes [Chuchu] Verduras [Acelga] Verduras [Agrião] Verduras [Alface] Verduras [Brócolis] Verduras [Chicória] Verduras [Couve Manteiga] Verduras [Couve-flor] Verduras [Escarola] Verduras [Espinafre] Verduras [Rúcula] Frutas cítricas [Laranja] Frutas cítricas [Tangerina/Mexerica/Bergamota] Frutas cítricas [Limão] Frutas cítricas [Abacaxi] Frutas cítricas [Acerola] Frutas cítricas [Morango] Frutas cítricas [Kiwi] Frutas cítricas [Maracujá] Outras frutas [Banana Nanica/Prata/Ouro/Maçã] Outras frutas [Goiaba] Outras frutas [Maçã] Outras frutas [Mamão] Outras frutas [Manga] Outras frutas [Melancia] Outras frutas [Melão] Outras frutas [Pera] Outras frutas [Pêssego]  \
5  1 Crepioca, ou bolacha de agua e sal. ( 16h)  1 fruta, ou 1 ovo mexido.// as vezes sopa de l...  bolacha, pão frances                                             Mensal                                             Não                         Mensal                      Mensal                         Mensal                         Não               Não               Não            Mensal              Mensal                 Não                    Mensal                Mensal                 NaN                  Não               Não                   Semanal                                         Mensal                 Semanal                    Mensal                       Não                       Não                 Mensal                        Não                                       Semanal                    Não              Semanal               Semanal                Mensal                   Mensal                Mensal                  Não                     Não   

  Outras frutas [Uva] Leguminos

In [13]:
for i, row in df_anamnese.iterrows():
    print(row.to_dict())

{'Carimbo de data/hora': datetime.datetime(2024, 4, 22, 11, 15, 34, 772000), 'Nome': 'Adriana Lucia de Souza', 'Número do prontuário': 8814, 'Tipo de atendimento': 'Avaliação', 'Data atendimento': datetime.datetime(2024, 4, 22, 0, 0), 'Data de nascimento': '28/04/1970', 'Idade': 53, 'Sexo': 'Feminino', 'Cidade e bairro que reside': 'São vicente.', 'Escolaridade': 'Ensino médio completo', 'Período em que trabalha/estuda': 'Não estuda', 'Há possibilidade de realizar lanches no local de estudo?': 'Não', 'Período em que trabalha': 'Não trabalha', 'Há a possibilidade de realizar lanches no local de trabalho?': 'Não', 'Profissão': 'Coopera', 'Renda familiar': '1 a 2 salários mínimos', 'Quantas pessoas moram no domicílio (contando com você)': 1, 'Motivo pela procura do ambulatório': 'Pela intolerância a lactose.', 'Apresenta alguma doença?': 'DM 2', 'Apresenta antecedentes familiares de alguma doença crônica? (DM, HAS, dislipidemia...)': 'a vó materna faleceu por cancer de utero, e a mãe fale

In [14]:
import pandas as pd
import numpy as np
from datetime import datetime

def generate_anamnese_insert_query(row):
    column_mapping = {
        'Nome': 'paciente_nome',
        'Escolaridade': 'escolaridade',
        'Período em que trabalha/estuda': 'periodo_estudo',
        'Há possibilidade de realizar lanches no local de estudo?': 'lanche_estudo',
        'Período em que trabalha': 'periodo_trabalho',
        'Há a possibilidade de realizar lanches no local de trabalho?': 'lanche_trabalho',
        'Profissão': 'profissao',
        'Renda familiar': 'renda_familiar',
        'Quantas pessoas moram no domicílio (contando com você)': 'num_pessoas_domicilio',
        'Motivo pela procura do ambulatório': 'motivo',
        'Apresenta alguma doença?': 'apresenta_doenca',
        'Frequência de evacuação': 'frequencia_evacuacao',
        'Consistência da evacuação:': 'consistencia_evacuacao',
        'Pratica atividade física regularmente?': 'pratica_atv_fisica',
        'Se sim: qual atividade, frequência semanal e duração? (intensidade,peso)': 'atv_fisica',
        'Café da manhã:': 'cafe_da_manha',
        'Lanche da manhã (se houver):': 'lanche_da_manha',
        'Almoço:': 'almoco',
        'Lanche da tarde:': 'lanche_da_tarde',
        'Jantar:': 'jantar',
        'Ceia (se houver):': 'ceia',
        # Adicione outros mapeamentos conforme necessário
        'Peso atual (kg)': 'peso_atual',
        'Estatura (m)': 'estatura',
        'IMC (kg/m²)': 'imc',
        'Dê uma nota à sua saciedade após as refeições': 'nota_saciedade_pos_refeicoes',
        'Como você classifica a sua satisfação pessoal (qualidade e quantidade da refeição) após realizar as refeições': 'nota_humor_pos_refeicoes',
        # Adicione outros mapeamentos conforme necessário
    }
    
    values = []
    
    # Preenchendo os valores com base no mapeamento
    for df_col, sql_col in column_mapping.items():
        value = row[df_col]
        if pd.isna(value):
            values.append('NULL')  # Para valores nulos
        elif isinstance(value, str):
            values.append(f"'{value.replace('\'', '\'\'')}'")  # Escapando aspas simples
        elif isinstance(value, (int, float)):
            values.append(str(value))  # Convertendo números para string
        elif isinstance(value, datetime):
            values.append(f"'{value.strftime('%Y-%m-%d %H:%M:%S')}'")  # Formatando datetime
        else:
            values.append('NULL')  # Para tipos não tratados

    # Montando a query
    query = f"""
    INSERT INTO anamnese (
        paciente_id, 
        usuario_id, 
        tipo_formulario, 
        escolaridade, 
        periodo_estudo, 
        lanche_estudo, 
        periodo_trabalho, 
        lanche_trabalho, 
        profissao, 
        renda_familiar, 
        num_pessoas_domicilio, 
        motivo, 
        apresenta_doenca, 
        frequencia_evacuacao, 
        consistencia_evacuacao, 
        pratica_atv_fisica, 
        atv_fisica, 
        cafe_da_manha, 
        lanche_da_manha, 
        almoco, 
        lanche_da_tarde, 
        jantar, 
        ceia, 
        peso_atual, 
        estatura, 
        imc, 
        nota_saciedade_pos_refeicoes, 
        nota_humor_pos_refeicoes, 
        criado_em
    ) VALUES (
        NULL,  -- paciente_id deve ser preenchido
        NULL,  -- usuario_id deve ser preenchido
        'Anamnese', 
        {values[1]},  -- escolaridade
        {values[2]},  -- periodo_estudo
        {values[3]},  -- lanche_estudo
        {values[4]},  -- periodo_trabalho
        {values[5]},  -- lanche_trabalho
        {values[6]},  -- profissao
        {values[7]},  -- renda_familiar
        {values[8]},  -- num_pessoas_domicilio
        {values[9]},  -- motivo
        {values[10]},  -- apresenta_doenca
        {values[11]},  -- frequencia_evacuacao
        {values[12]},  -- consistencia_evacuacao
        {values[13]},  -- pratica_atv_fisica
        {values[14]},  -- atv_fisica
        {values[15]},  -- cafe_da_manha
        {values[16]},  -- lanche_da_manha
        {values[17]},  -- almoco
        {values[18]},  -- lanche_da_tarde
        {values[19]},  -- jantar
        {values[20]},  -- ceia
        {values[21]},  -- peso_atual
        {values[22]},  -- estatura
        {values[23]},  -- imc
        {values[24]},  -- nota_saciedade_pos_refeicoes
        {values[25]},  -- nota_humor_pos_refeicoes
        CURRENT_TIMESTAMP  -- criado_em
    );
    """
    
    return query.strip()

# Exemplo de uso
# df = pd.DataFrame(...)  # Seu DataFrame aqui
# row = df.iloc[0]  # Pegando a primeira linha como exemplo
query = generate_anamnese_insert_query(row)
print(query)

INSERT INTO anamnese (
        paciente_id, 
        usuario_id, 
        tipo_formulario, 
        escolaridade, 
        periodo_estudo, 
        lanche_estudo, 
        periodo_trabalho, 
        lanche_trabalho, 
        profissao, 
        renda_familiar, 
        num_pessoas_domicilio, 
        motivo, 
        apresenta_doenca, 
        frequencia_evacuacao, 
        consistencia_evacuacao, 
        pratica_atv_fisica, 
        atv_fisica, 
        cafe_da_manha, 
        lanche_da_manha, 
        almoco, 
        lanche_da_tarde, 
        jantar, 
        ceia, 
        peso_atual, 
        estatura, 
        imc, 
        nota_saciedade_pos_refeicoes, 
        nota_humor_pos_refeicoes, 
        criado_em
    ) VALUES (
        NULL,  -- paciente_id deve ser preenchido
        NULL,  -- usuario_id deve ser preenchido
        'Anamnese', 
        'Ensino médio completo',  -- escolaridade
        'Não estuda',  -- periodo_estudo
        'Não',  -- lanche_estudo
        'Não traba